In [22]:
import numpy as np
import matplotlib.pyplot as plt
import rasterio
import pandas as pd
import geopandas as gpd
from tqdm.auto import tqdm
import os
import shapely.geometry
import joblib

def load_labels_data():
    file_path = './data/joblibs/labels.joblib'
    gdf = joblib.load(file_path)
    gdf = gdf.to_crs(crs='EPSG:4326')
    return gdf
def shapely_point(lat, lon):
    return shapely.geometry.Point(lon, lat)
def get_available_data_dataframe():
    satellite_images_dir = './data/satellite_images'
    downloaded_dates = os.listdir(satellite_images_dir)
    #remove dates if they are not in YYYY-MM-DD format
    downloaded_dates = [date for date in downloaded_dates if len(date) == 10]
    downloaded_dates = sorted(downloaded_dates)
    downloaded_data_dict = {
        'date': [],
        'location': [],
        'evalscript': [],
        'identifier': [],
        'file_name': []
    }
    for date in downloaded_dates:
        date_dir = os.path.join(satellite_images_dir, date)
        locations = os.listdir(date_dir)
        for location in locations:
            location_dir = os.path.join(date_dir, location)
            evalscripts = os.listdir(location_dir)
            for evalscript in evalscripts:
                evalscript_dir = os.path.join(location_dir, evalscript)
                identifiers = os.listdir(evalscript_dir)
                for identifier in identifiers:
                    identifier_dir = os.path.join(evalscript_dir, identifier)
                    file_names = os.listdir(identifier_dir)
                    for file_name in file_names:
                        if file_name.startswith('response'):
                            downloaded_data_dict['date'].append(date)
                            downloaded_data_dict['location'].append(location)
                            downloaded_data_dict['evalscript'].append(evalscript)
                            downloaded_data_dict['identifier'].append(identifier)
                            downloaded_data_dict['file_name'].append(file_name)
    downloaded_data = pd.DataFrame(downloaded_data_dict)
    return downloaded_data
def get_image_path_from_row(row):
    date = row['date']
    location = row['location']
    evalscript = row['evalscript']
    identifier = row['identifier']
    file_name = row['file_name']
    image_path = f'./data/satellite_images/{date}/{location}/{evalscript}/{identifier}/{file_name}'
    return image_path
def read_image_with_rasterio(image_path):
    img = rasterio.open(image_path)
    return img
def rastrio_img(df, index):
    row = df.iloc[index]
    img_path = get_image_path_from_row(row)
    img = read_image_with_rasterio(img_path)
    return img
def get_lats_lons_from_raster(src):
    band1 = src.read(1)
    height = band1.shape[0]
    width = band1.shape[1]
    cols, rows = np.meshgrid(np.arange(width), np.arange(height))
    xs, ys = rasterio.transform.xy(src.transform, rows, cols)
    lons= np.array(xs)
    lats = np.array(ys)
    return lats, lons
def gdf_from_raster(src, bands_names=None):
    lats, lons = get_lats_lons_from_raster(src)
    img_array = np.array(src.read())
    if bands_names is None:
        bands_names = [f'B{i}' for i in range(src.count)]
    lats = lats.flatten()
    lons = lons.flatten()
    img_array = img_array.reshape((img_array.shape[0], img_array.shape[1]*img_array.shape[2]))
    df = pd.DataFrame(img_array.T, columns=bands_names)
    df['Lat'] = lats
    df['Lon'] = lons
    geom = []
    for i in tqdm(range(len(df))):
        p = shapely_point(lats[i], lons[i]) 
        geom.append(p)
    gdf = gpd.GeoDataFrame(df, geometry=geom)
    gdf.crs = src.crs
    gdf = gdf.to_crs('EPSG:4326')
    gdf = gdf.reset_index(drop=True)
    return gdf
def get_gdf_from_row(df, row, bands_names=None):
    src = rastrio_img(df, row)
    gdf = gdf_from_raster(src, bands_names)
    return gdf

In [23]:
images_paths_df = get_available_data_dataframe()
locations = images_paths_df['location'].values
locations_indeices = [i for i in range(len(locations)) if locations[i].startswith('gaizera_square_45X45')]
images_paths_df = images_paths_df.iloc[locations_indeices]
dates = images_paths_df['date'].values
dates_indeices = [i for i in range(len(dates)) if dates[i].startswith('2021-')]
images_paths_df = images_paths_df.iloc[dates_indeices]
evalscripts = images_paths_df['evalscript'].values
evalscripts_indeices = [i for i in range(len(evalscripts)) if evalscripts[i] in ['ALL', 'FCOVER']]
images_paths_df = images_paths_df.iloc[evalscripts_indeices]
images_paths_df

date                 location evalscript  \
50    2021-06-01   gaizera_square_45X45_0        ALL   
52    2021-06-01   gaizera_square_45X45_0     FCOVER   
55    2021-06-01   gaizera_square_45X45_1        ALL   
57    2021-06-01   gaizera_square_45X45_1     FCOVER   
60    2021-06-01  gaizera_square_45X45_10        ALL   
...          ...                      ...        ...   
2096  2021-09-19   gaizera_square_45X45_8     FCOVER   
2099  2021-09-19  gaizera_square_45X45_80        ALL   
2101  2021-09-19  gaizera_square_45X45_80     FCOVER   
2104  2021-09-19   gaizera_square_45X45_9        ALL   
2106  2021-09-19   gaizera_square_45X45_9     FCOVER   

                            identifier      file_name  
50    cee045ea896a01a814ca42d7697b08a4  response.tiff  
52    d2086f71b35388f0302d9cc2fa1a1ee7  response.tiff  
55    5af865f9187bc1b0c3094d6a6131f83a  response.tiff  
57    0acf4160273eb598207b1e1c7ececf8d  response.tiff  
60    0e33c77fb197b0c44f3b2ca45c676182  response.tiff  
...                                ...            ...  
2096  d40c59fea113b191f7f01a05f018d458  response.tiff  
2099  0166521e47a1598964a1b9e013393e1d  response.tiff  
2101  8572924f61b1aa073aa16d39131031e2  response.tiff  
2104  4597148242c759f416cfca2b9d31cfbe  response.tiff  
2106  b133ca754087806bb1f5e566fd19e141  response.tiff  

[648 rows x 5 columns]

In [24]:
current_location = 'gaizera_square_45X45_0'
current_date = '2021-06-01'
current_evalscript = 'ALL'

current_df = images_paths_df[(images_paths_df['location'] == current_location) & (images_paths_df['date'] == current_date) & (images_paths_df['evalscript'] == current_evalscript)]
current_df = current_df.reset_index(drop=True)
current_df

date                location evalscript  \
0  2021-06-01  gaizera_square_45X45_0        ALL   

                         identifier      file_name  
0  cee045ea896a01a814ca42d7697b08a4  response.tiff

In [25]:
bands_all = ['B01', 'B02', 'B03', 'B04', 'B05', 'B06', 'B07', 'B08','B8A', 'B09', 'B10', 'B11', 'B12']
gdf = get_gdf_from_row(current_df, 0, bands_names=bands_all)
gdf


  0%|          | 0/4960662 [00:00<?, ?it/s]

B01     B02     B03     B04     B05     B06     B07     B08  \
0        0.1541  0.1406  0.1436  0.1659  0.1761  0.2048  0.2406  0.2387   
1        0.1541  0.1416  0.1433  0.1648  0.1723  0.1979  0.2212  0.2373   
2        0.1541  0.1423  0.1402  0.1595  0.1723  0.1979  0.2212  0.2088   
3        0.1529  0.1434  0.1392  0.1575  0.1652  0.1849  0.2089  0.1989   
4        0.1529  0.1414  0.1390  0.1560  0.1652  0.1849  0.2089  0.2074   
...         ...     ...     ...     ...     ...     ...     ...     ...   
4960657  0.1700  0.1678  0.1782  0.2111  0.2167  0.2476  0.2831  0.2860   
4960658  0.1700  0.1693  0.1736  0.2072  0.2167  0.2476  0.2831  0.2803   
4960659  0.1700  0.1774  0.1936  0.2405  0.2434  0.2710  0.3101  0.2975   
4960660  0.1700  0.1841  0.1998  0.2523  0.2434  0.2710  0.3101  0.3178   
4960661  0.1700  0.1777  0.1932  0.2451  0.2333  0.2627  0.2977  0.3027   

            B8A     B09     B10     B11     B12        Lat        Lon  \
0        0.2713  0.0555  0.0013  0.2667  0.1897  13.746268  32.350270   
1        0.2504  0.0555  0.0013  0.2705  0.1954  13.746268  32.350363   
2        0.2504  0.0555  0.0013  0.2705  0.1954  13.746268  32.350455   
3        0.2316  0.0532  0.0014  0.2674  0.1986  13.746268  32.350547   
4        0.2316  0.0532  0.0014  0.2674  0.1986  13.746268  32.350639   
...         ...     ...     ...     ...     ...        ...        ...   
4960657  0.3168  0.0652  0.0015  0.3421  0.2407  13.551134  32.562338   
4960658  0.3168  0.0652  0.0015  0.3421  0.2407  13.551134  32.562431   
4960659  0.3441  0.0652  0.0015  0.3644  0.2546  13.551134  32.562523   
4960660  0.3441  0.0652  0.0015  0.3644  0.2546  13.551134  32.562615   
4960661  0.3277  0.0652  0.0015  0.3562  0.2477  13.551134  32.562707   

                          geometry  
0        POINT (32.35027 13.74627)  
1        POINT (32.35036 13.74627)  
2        POINT (32.35045 13.74627)  
3        POINT (32.35055 13.74627)  
4        POINT (32.35064 13.74627)  
...                            ...  
4960657  POINT (32.56234 13.55113)  
4960658  POINT (32.56243 13.55113)  
4960659  POINT (32.56252 13.55113)  
4960660  POINT (32.56262 13.55113)  
4960661  POINT (32.56271 13.55113)  

[4960662 rows x 16 columns]

In [ ]:
labels_gdf = load_labels_data()

states = labels_gdf['State'].values
states_indeices = [i for i in range(len(states)) if states[i].startswith('squares_2000')]
labels_gdf = labels_gdf.iloc[states_indeices]
labels_gdf = labels_gdf.reset_index(drop=True)

In [35]:
from tqdm.auto import tqdm
def point_in_gdf(point, gdf):
    in_gdf = gdf.geometry.contains(point)
    if in_gdf.sum() > 0:
        return True    
    return False

points = gdf.geometry.values
points_in_labels = []
points_in_labels_indices = []
for i in tqdm(range(len(points))):
    point = points[i]
    if point_in_gdf(point, labels_gdf):
        points_in_labels.append(point)
        points_in_labels_indices.append(i)
    if len(points_in_labels)%10 == 0 and len(points_in_labels) > 0:
        print(len(points_in_labels))
    if len(points_in_labels) == 1:
        print('first point in labels')
        


  0%|          | 0/4960662 [00:00<?, ?it/s]

first point in labels
10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290
290

In [36]:
points_in_labels = np.array(points_in_labels)
points_in_labels_indices = np.array(points_in_labels_indices)
dict_points_in_labels = {
    'point': points_in_labels,
    'index': points_in_labels_indices
}
path = f'./data/joblibs/poinst_in_labels_{current_location}_{current_date}_{current_evalscript}.joblib'
joblib.dump(dict_points_in_labels, path)

['./data/joblibs/poinst_in_labels_gaizera_square_45X45_0_2021-06-01_ALL.joblib']

Rainfed                                           geometry  \
0          -1  POLYGON ((32.76939 14.07349, 32.76939 14.07574...   
1          -1  POLYGON ((33.92607 13.56460, 33.92607 13.56685...   
2          -1  POLYGON ((32.35553 13.68394, 32.35553 13.68619...   
3          -1  POLYGON ((32.41920 15.03723, 32.41920 15.03948...   
4          -1  POLYGON ((34.14361 14.56437, 34.14361 14.56662...   
...       ...                                                ...   
1995       -1  POLYGON ((34.22054 15.26466, 34.22054 15.26691...   
1996       -1  POLYGON ((32.67123 13.96090, 32.67123 13.96316...   
1997       -1  POLYGON ((34.17014 14.76928, 34.17014 14.77153...   
1998       -1  POLYGON ((34.11973 13.87309, 34.11973 13.87534...   
1999       -1  POLYGON ((32.73755 14.42476, 32.73755 14.42701...   

                                  State  Year fieldID Crop_Type imgPaths bbox  \
0        squares_2000_0.5x0.5_gaizera_0  2023     NaN     Other      NaN  NaN   
1        squares_2000_0.5x0.5_gaizera_1  2023     NaN     Other      NaN  NaN   
2        squares_2000_0.5x0.5_gaizera_2  2023     NaN     Other      NaN  NaN   
3        squares_2000_0.5x0.5_gaizera_3  2023     NaN     Other      NaN  NaN   
4        squares_2000_0.5x0.5_gaizera_4  2023     NaN     Other      NaN  NaN   
...                                 ...   ...     ...       ...      ...  ...   
1995  squares_2000_0.5x0.5_gaizera_1995  2023     NaN     Other      NaN  NaN   
1996  squares_2000_0.5x0.5_gaizera_1996  2023     NaN     Other      NaN  NaN   
1997  squares_2000_0.5x0.5_gaizera_1997  2023     NaN     Other      NaN  NaN   
1998  squares_2000_0.5x0.5_gaizera_1998  2023     NaN     Other      NaN  NaN   
1999  squares_2000_0.5x0.5_gaizera_1999  2023     NaN     Other      NaN  NaN   

      FID Block_No Class Sowing_dat       Area_M2 Name  
0     NaN      NaN   NaN        NaN  71379.813094  NaN  
1     NaN      NaN   NaN        NaN  71531.994910  NaN  
2     NaN      NaN   NaN        NaN  71496.801805  NaN  
3     NaN      NaN   NaN        NaN  71076.505153  NaN  
4     NaN      NaN   NaN        NaN  71227.792121  NaN  
...   ...      ...   ...        ...           ...  ...  
1995  NaN      NaN   NaN        NaN  71002.052582  NaN  
1996  NaN      NaN   NaN        NaN  71413.957100  NaN  
1997  NaN      NaN   NaN        NaN  71162.817668  NaN  
1998  NaN      NaN   NaN        NaN  71440.401951  NaN  
1999  NaN      NaN   NaN        NaN  71271.549159  NaN  

[2000 rows x 14 columns]

In [28]:
labels_gdf.State.value_counts()

Mangil                              6270
Gaziera                             2894
Qadarif                              209
BlueNile1                             48
BlueNile2                             39
                                    ... 
squares_2000_0.5x0.5_gaizera_676       1
squares_2000_0.5x0.5_gaizera_675       1
squares_2000_0.5x0.5_gaizera_674       1
squares_2000_0.5x0.5_gaizera_673       1
squares_81_45x45_gaizera_80            1
Name: State, Length: 2104, dtype: int64

In [1]:
import geopandas as gpd
from pyproj import Geod
import shapely.geometry
import folium
import numpy as np
import joblib
from tqdm import tqdm
import new_app

def get_dictionary_of_images_from_evalscripts(total_polygon, date, location_name):
    eval_true_color = 'TRUECOLOR'
    eval_CLP = 'CLP'
    eval_FCOVER = 'FCOVER'
    eval_all = 'ALL'
    eval_ndvi = 'NDVI'
    all, all_dir = new_app.get_any_image_from_sentinelhub(total_polygon, date, eval_all, location_name)
    tc, tc_dir = new_app.get_any_image_from_sentinelhub(total_polygon, date, eval_true_color, location_name)
    clp, clp_dir = new_app.get_any_image_from_sentinelhub(total_polygon, date, eval_CLP, location_name)
    fcover, fcover_dir = new_app.get_any_image_from_sentinelhub(total_polygon, date, eval_FCOVER, location_name)
    ndvi, ndvi_dir = new_app.get_any_image_from_sentinelhub(total_polygon, date, eval_ndvi, location_name)
    images_dict = {
        'all': all,
        'all_dir': all_dir,
        'tc': tc,
        'tc_dir': tc_dir,
        'clp': clp,
        'clp_dir': clp_dir,
        'fcover': fcover,
        'fcover_dir': fcover_dir,
        'ndvi': ndvi,
        'ndvi_dir': ndvi_dir
    }
    return images_dict

def calculate_area_in_square_meters(geometry):
    geod = Geod(ellps="WGS84")
    area = abs(geod.geometry_area_perimeter(geometry)[0])
    return area

def states_gdf_from_geojson(file_path = './data/geojsons/sudan_states.geojson'):
    gdf = gpd.read_file(file_path)
    gdf = gdf.to_crs(crs='EPSG:4326')
    gdf['Area_M2'] = gdf['geometry'].apply(calculate_area_in_square_meters)
    gdf.rename(columns={'admin1RefN':'State'}, inplace=True)
    gdf = gdf[['State', 'Area_M2', 'geometry']]
    return gdf

def filter_by_state(gdf, state_name='El Gazira'):
    gdf = gdf[gdf['State'] == state_name]
    gdf.reset_index(inplace=True)
    gdf.drop(columns='index', inplace=True)
    return gdf

def save_gdf_to_geojson(gdf, file_path='./data/geojsons/sudan_states_2.geojson'):
    gdf.to_file(file_path, driver='GeoJSON')

def get_bbox_info(gdf):
    geod = Geod(ellps="WGS84")
    bbox = gdf.total_bounds
    polygon = shapely.geometry.box(*bbox, ccw=True)
    area = abs(geod.geometry_area_perimeter(polygon)[0])
    perimeter = abs(geod.geometry_area_perimeter(polygon)[1])
    width_line_coords = [(bbox[1], bbox[0]), (bbox[1], bbox[2])]
    width_line = shapely.geometry.LineString(width_line_coords)
    width = abs(geod.geometry_area_perimeter(width_line)[1])
    height_line_coords = [(bbox[1], bbox[0]), (bbox[3], bbox[0])]
    height_line = shapely.geometry.LineString(height_line_coords)
    height = abs(geod.geometry_area_perimeter(height_line)[1])
    gdf_bbox = gdf.total_bounds
    gdf_bbox_polygon = shapely.geometry.box(*gdf_bbox, ccw=True)
    gdf_bbox = [(gdf_bbox[1], gdf_bbox[0]), (gdf_bbox[3], gdf_bbox[2])]
    return width, height, area, perimeter, gdf_bbox 

def get_square_list_for_state(gdf, max_width=25, max_height=25):
    max_width = max_width*1000
    max_height = max_height*1000
    width, height, area, perimeter, state_bbox = get_bbox_info(gdf)
    bottom_left = state_bbox[0]
    top_right = state_bbox[1]
    y_axis_max = top_right[0]
    y_axis_min = bottom_left[0]
    x_axis_max = top_right[1]
    x_axis_min = bottom_left[1]
    width_ratio = width/max_width
    if width_ratio > 1:
        number_of_widths = np.ceil(width_ratio)
        distance_between_widths = (x_axis_max - x_axis_min)/number_of_widths
        new_ys = np.arange(y_axis_min, y_axis_max, distance_between_widths)
        new_xs_left = np.repeat(x_axis_min, len(new_ys))
        new_xs_right = np.repeat(x_axis_max, len(new_ys))
    height_ratio = height/max_height
    if height_ratio > 1:
        number_of_heights = np.ceil(height_ratio)
        distance_between_heights = (y_axis_max - y_axis_min)/number_of_heights
        new_xs = np.arange(x_axis_min, x_axis_max, distance_between_heights)
        new_ys_bottom = np.repeat(y_axis_min, len(new_xs))
        new_ys_top = np.repeat(y_axis_max, len(new_xs))
    intersection_rows = []
    for x in tqdm(new_xs):
        intersection_points = []
        for y in new_ys:
            p = (y, x)
            intersection_points.append(p)
        intersection_rows.append(intersection_points)
    new_squares = []
    for row_index in tqdm(range(len(intersection_rows)-1)):
        row = intersection_rows[row_index]
        next_row = intersection_rows[row_index+1]
        for point_index in range(len(row)-1):
            point = row[point_index]
            next_point = row[point_index+1]
            next_row_point = next_row[point_index]
            next_row_next_point = next_row[point_index+1]
            square = [point, next_point, next_row_next_point, next_row_point]
            new_squares.append(square)
    return new_squares

def convert_square_to_polygon(square):
    new_points = []
    for point in square:
        new_point = (point[1], point[0])
        new_points.append(new_point)
    new_points.append(new_points[0])
    polygon = shapely.geometry.Polygon(new_points)
    return polygon

def gdf_from_square_list(square_list, location='gaizera'):
    geom = []
    for square in tqdm(square_list):
        polygon = convert_square_to_polygon(square)
        geom.append(polygon)
    gdf = gpd.GeoDataFrame(geometry=geom)
    gdf.crs = "EPSG:4326"
    gdf['square_id'] = [f'{location}_{i}' for i in range(len(gdf))]
    gdf['Area_M2'] = gdf['geometry'].apply(calculate_area_in_square_meters)
    gdf['Area_KM2'] = gdf['Area_M2']/1000000
    gdf['location'] = location
    return gdf

def main_inf(max_width=30, max_height=30, num_squares=1):
    gdf = states_gdf_from_geojson(file_path='./data/geojsons/sudan_states_gaziera.geojson')
    new_squares = get_square_list_for_state(gdf, max_width=max_width, max_height=max_height)
    if num_squares == -1 or num_squares > len(new_squares):
        num_squares = len(new_squares)
    random_indices = np.random.choice(len(new_squares), num_squares, replace=False)
    new_squares = [new_squares[i] for i in random_indices]
    gdf_sq = gdf_from_square_list(new_squares, location='gaizera')
    gdf_sq['Width'] = max_width
    gdf_sq['Height'] = max_height
    file_name = f'./data/joblibs/squares_{len(gdf_sq)}_{max_width}x{max_height}_gaizera.joblib'
    joblib.dump(gdf_sq, file_name)
    return gdf_sq

def seq_inside(gdf_sq, gdf):
    withins = []
    for i in tqdm(range(len(gdf_sq))):
        gdf_sq_i = gdf_sq.iloc[i:i+1]
        gdf_sq_i.reset_index(inplace=True, drop=True)
        inisde = gdf_sq_i.within(gdf).values[0]
        if inisde:
            withins.append(1)
        else:
            withins.append(0)
    return withins

In [2]:
gdf_sq = joblib.load('./data/joblibs/squares_81_45x45_gaizera.joblib')
gdf = states_gdf_from_geojson(file_path='./data/geojsons/sudan_states_gaziera.geojson')
gdf_sq['inside'] = seq_inside(gdf_sq, gdf)

100%|██████████| 81/81 [00:00<00:00, 191.67it/s]


In [3]:
for i in tqdm(range(len(gdf_sq))):
    gdf_sq_i = gdf_sq.iloc[i:i+1]
    gdf_sq_i.reset_index(inplace=True, drop=True)
    date = '2023-06-01'
    total_bounds = gdf_sq_i.total_bounds
    total_polygon = shapely.geometry.box(*total_bounds, ccw=True)
    d = get_dictionary_of_images_from_evalscripts(total_polygon, date, f'gaizera_square_45X45_{i}')


100%|██████████| 81/81 [1:58:17<00:00, 87.63s/it] 


In [4]:
dates = [
    '2023-06-01',
    '2023-07-16',
    '2023-08-15',
    '2023-09-09',
]
for date in dates:
    for i in tqdm(range(len(gdf_sq))):
        gdf_sq_i = gdf_sq.iloc[i:i+1]
        gdf_sq_i.reset_index(inplace=True, drop=True)
        total_bounds = gdf_sq_i.total_bounds
        total_polygon = shapely.geometry.box(*total_bounds, ccw=True)
        d = get_dictionary_of_images_from_evalscripts(total_polygon, date, f'gaizera_square_45X45_{i}')

 33%|███▎      | 27/81 [31:41<1:02:01, 68.91s/it]c:\Users\Edin\anaconda3\envs\amazon\lib\site-packages\sentinelhub\download\sentinelhub_client.py:87: SHRateLimitWarning: Download rate limit hit
  warnings.warn("Download rate limit hit", category=SHRateLimitWarning)
 35%|███▍      | 28/81 [32:46<59:41, 67.58s/it]  c:\Users\Edin\anaconda3\envs\amazon\lib\site-packages\sentinelhub\download\sentinelhub_client.py:87: SHRateLimitWarning: Download rate limit hit
  warnings.warn("Download rate limit hit", category=SHRateLimitWarning)
 36%|███▌      | 29/81 [33:53<58:34, 67.59s/it]c:\Users\Edin\anaconda3\envs\amazon\lib\site-packages\sentinelhub\download\sentinelhub_client.py:87: SHRateLimitWarning: Download rate limit hit
  warnings.warn("Download rate limit hit", category=SHRateLimitWarning)
 37%|███▋      | 30/81 [34:58<56:37, 66.61s/it]c:\Users\Edin\anaconda3\envs\amazon\lib\site-packages\sentinelhub\download\sentinelhub_client.py:87: SHRateLimitWarning: Download rate limit hit
  warnings.w

In [4]:
# dates = [
#     '2023-06-01',
#     '2023-07-16',
#     '2023-08-15',
#     '2023-09-09',
# ]
# for date in dates:
#     print(date)
#     for i in tqdm(range(len(gdf_sq))):
#         gdf_sq_i = gdf_sq.iloc[i:i+1]
#         gdf_sq_i.reset_index(inplace=True, drop=True)
#         total_bounds = gdf_sq_i.total_bounds
#         total_polygon = shapely.geometry.box(*total_bounds, ccw=True)
#         d = get_dictionary_of_images_from_evalscripts(total_polygon, date, f'gaizera_square_45X45_{i}')

# dates = [
#     '2022-06-01',
#     '2022-07-06',
#     '2022-08-10',
#     '2022-09-14',
# ]
# for date in dates:
#     print(date)
#     for i in tqdm(range(len(gdf_sq))):
#         gdf_sq_i = gdf_sq.iloc[i:i+1]
#         gdf_sq_i.reset_index(inplace=True, drop=True)
#         total_bounds = gdf_sq_i.total_bounds
#         total_polygon = shapely.geometry.box(*total_bounds, ccw=True)
#         d = get_dictionary_of_images_from_evalscripts(total_polygon, date, f'gaizera_square_45X45_{i}')

dates = [
    # '2021-06-01',
    # '2021-07-16',
    # '2021-08-05',
    '2021-09-19',
]
for date in dates:
    print(date)
    for i in tqdm(range(len(gdf_sq))):
        gdf_sq_i = gdf_sq.iloc[i:i+1]
        gdf_sq_i.reset_index(inplace=True, drop=True)
        total_bounds = gdf_sq_i.total_bounds
        total_polygon = shapely.geometry.box(*total_bounds, ccw=True)
        d = get_dictionary_of_images_from_evalscripts(total_polygon, date, f'gaizera_square_45X45_{i}')

2021-09-19


100%|██████████| 81/81 [38:57<00:00, 28.86s/it]


In [ ]:
import matplotlib.pyplot as plt
true_color = d['tc']
true_color_dir = d['tc_dir']

fig = plt.figure(figsize=(20, 20))
plt.imshow(true_color)

In [ ]:
true_color.shape